La empresa desea saber si tiene los recursos necesarios para soportar la demanda de los usuarios e
incrementar el numero de ticktes por día. En base a ello, diseñe y desarrolle un modelo y/o script que
permita realizar la simulación del proceso de pasar cuenca-aire con las siguientes especificaciones

- La empresa tiene 3 carriles de revisión vehicular
- Un solo carril es habilitado para carros de gran tonelaje, busetas, bus, camiones, solo el 15 % de vehiculos que llegan son de este tipo.
- Cada 3 minutos llega un nuevo vehiculo a revision.
- Se sigue el siguiente proceso:

1) Llega el vehiculo al centro, se estaciona (3-5 minutos), saca un turno (1-3 minutos) y pagan
la matricula (5 - 10 minutos).
2) Si esta vacio pasa directo a la revisión que tiene una media de 20 minutos con una
desviacion estandar de 10 minutos.
3) Solo el 60 % de vehiculos pasa sin ninguna notificación, el 40% salen realizan el arreglo (2
dias) y nuevamente realizan el proceso.
4) Despues de pasar la revisión, se les pega el sello (1 – 3 minutos) .
5) Finalmente, salen (5 – 10 minutos).
Generar un modelo de simulación por 30 dias y generar las siguientes graficas de resultados:
- Numero de vehiculos atendidos por dia, y por carril
- Porcentaje total de vehiculos aprobados y no aprobados en cuenca aire por dia.
- Tiempos del proceso de matriculación, por dia.


In [3]:
import simpy
import random
import math 
import numpy as np 



tiempoDias= 30

tiempoRev = 3

tiempoEjecucion= 43200  # 30 dias

num_c_livianos=2
num_c_pesados = 1

vahiculos_dañados=[]

class EMOV(object):
    
    def __init__(self, environment, num_c_livianos, num_c_pesados):
        # Guardamos como variable el entorno de ejecucion
        self.env=environment
        # Creamos el recurso que representa las maquinas
        self.maquinasL = simpy.Resource(environment, num_c_livianos)
        self.maquinasP = simpy.Resource(environment, num_c_pesados)
        


        
    def matricular_pesado(self, vehiculo):
        mu, sigma = 20, 10 # media y desvio estandar
        tiempo = abs(math.ceil(np.random.normal(mu, sigma, 1))) #media de 20 minutos con una desviacion estandar de 10 minutos.
        yield self.env.timeout(tiempo)

        print('El vehiculo vehiculo %s a tardado %s minutos en la revicion' % (vehiculo, tiempo))

    def matricular_liviano(self, vehiculo):
        mu, sigma = 20, 10 # media y desvio estandar
        tiempo = abs(math.ceil(np.random.normal(mu, sigma, 1))) #media de 20 minutos con una desviacion estandar de 10 minutos.
        yield self.env.timeout(tiempo)

        print('El vehiculo vehiculo %s a tardado %s minutos en la revicion' % (vehiculo, tiempo))


       

def generar_auto():
    num = random.randint(1,100)

    if num <= 15:
        num2 = random.randint(0,2)
        gt = ["Buseta", "Bus", "Camion"]
        return gt[num2]
    else:
        num2 = random.randint(0,2)
        tipos = ["Camioneta","Automóvil","Jeep"]
        return tipos[num2]



def llegada_vehiculo(env, nombre, emov):
    t=0
    print('Llega : %s a la hora %.2f.' % (nombre, env.now))
    t=random.randint(3,5)
    yield env.timeout(t)
    print(' %s Espero estacionado por: %s minutos (Hora Actual: %.2f.)' % (nombre, t, env.now))
    t=random.randint(1,3)
    yield env.timeout(t)
    print(' %s Saco su turno en: %s minutos (Hora Actual: %.2f.)' % (nombre, t, env.now))
    t=random.randint(5,10)
    yield env.timeout(t)
    print(' %s Pago su matricula, tardandose: %s minutos (Hora Actual: %.2f.)' % (nombre, t, env.now))




    if "Buseta" or "Bus" or "Camion" in nombre: 

        with emov.maquinasP.request() as maquinaP:
            yield maquinaP
            print('Revisandose: %s a la hora %.2f en carril para vehiculos de Gran Tonelaje.' % (nombre, env.now))
            
            yield env.process(emov.matricular_pesado(nombre))
            
            num = random.randint(1,100)
            if num <= 40:
                print('!!!!! El Carro: %s No cumple con los requisitos!!!!! (Hora %.2f)' % (nombre, env.now))
                vahiculos_dañados.append(nombre)
                i_will_be_back(env,nombre,emov)
            else:
                print('El Carro: %s cumple con los requisitos ☻ (Hora %.2f)' % (nombre, env.now))
                proceso_salida(env,nombre)        
    else: 
        with emov.maquinasL.request() as maquinaL:
            yield maquinaL
            print('Revisandose: %s a la hora %.2f en uno de  los carriles para vehiculos pequeños.' % (nombre, env.now))
            
            yield env.process(emov.matricular_liviano(nombre))
            
            num = random.randint(1,100)
            if num <= 40:
                print('!!!!! El Carro: %s No cumple con los requisitos!!!!! (Hora %.2f)' % (nombre, env.now))
                vahiculos_dañados.append(nombre)
                i_will_be_back(env,nombre,emov)
            else:
                print('El Carro: %s cumple con los requisitos ☻ (Hora %.2f)' % (nombre, env.now))
                proceso_salida(env,nombre)  

    
def i_will_be_back(env,nombre,emov):
    yield env.timeout(2880)
    llegada_vehiculo(env,nombre,emov)


def proceso_salida(env,nombre):
    t=random.randint(1,3)
    yield env.timeout(t)
    print('El Carro: %s recibe un sello en %x Minutos' % (nombre, t))
    t=random.randint(1,3)
    yield env.timeout(t)
    print('El Carro: %s salio del establecimiento en %x Minutos (Hora: hora %.2f)' % (nombre, t, env.now))




def ejecutar_simulacion(env, num_c_livianos, num_c_pesados):
    emov=EMOV(env, num_c_livianos, num_c_pesados)

    i=0
    # Ejecutamos la simulacion
    while True:                  #Floro Intervalo de 1 a 2 
        yield env.timeout(3)
        i+=1
        # Mientras se lavan los vehiculos generamos mas vehiculos
                                               #Floro
        env.process(llegada_vehiculo(env,str(generar_auto())+'-%d'%(i),emov))










env=simpy.Environment()
env.process(ejecutar_simulacion(env, num_c_livianos, num_c_pesados))
env.run(until = tiempoEjecucion)

print(vahiculos_dañados)


Llega : Buseta-1 a la hora 3.00.
Llega : Buseta-2 a la hora 6.00.
 Buseta-1 Espero estacionado por: 5 minutos (Hora Actual: 8.00.)
Llega : Camioneta-3 a la hora 9.00.
 Buseta-1 Saco su turno en: 2 minutos (Hora Actual: 10.00.)
 Buseta-2 Espero estacionado por: 5 minutos (Hora Actual: 11.00.)
Llega : Camion-4 a la hora 12.00.
 Buseta-2 Saco su turno en: 2 minutos (Hora Actual: 13.00.)
 Camioneta-3 Espero estacionado por: 5 minutos (Hora Actual: 14.00.)
Llega : Camioneta-5 a la hora 15.00.
 Camion-4 Espero estacionado por: 5 minutos (Hora Actual: 17.00.)
 Camioneta-3 Saco su turno en: 3 minutos (Hora Actual: 17.00.)
 Buseta-2 Pago su matricula, tardandose: 5 minutos (Hora Actual: 18.00.)
Llega : Automóvil-6 a la hora 18.00.
Revisandose: Buseta-2 a la hora 18.00 en carril para vehiculos de Gran Tonelaje.
 Buseta-1 Pago su matricula, tardandose: 9 minutos (Hora Actual: 19.00.)
 Camioneta-5 Espero estacionado por: 4 minutos (Hora Actual: 19.00.)
 Camion-4 Saco su turno en: 3 minutos (Hora A